In [0]:
import pyspark.sql.functions as F
from pyspark.sql.types import FloatType, IntegerType

from pyspark.ml import Pipeline
from pyspark.ml.feature import StringIndexer, OneHotEncoder, VectorAssembler
from pyspark.ml.classification import RandomForestClassifier, LogisticRegression
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
from pyspark.mllib.evaluation import MulticlassMetrics

# Data preparation

In [0]:
recipes = spark.read.option("sep", ",").option("quote", "\"").option("escape", "\"").option("header", "true").option("multiline", "true").csv("wasb://workfront@buyingcirclestorage.blob.core.windows.net/recipe/recipes.csv")
reviews = spark.read.option("sep", ",").option("quote", "\"").option("escape", "\"").option("header", "true").option("multiline", "true").csv("wasb://workfront@buyingcirclestorage.blob.core.windows.net/recipe/reviews.csv")

In [0]:
recipes.createOrReplaceTempView("recipes")
reviews.createOrReplaceTempView("reviews")

In [0]:
%sql
select *
from recipes
limit 100

RecipeId Name AuthorId AuthorName CookTime PrepTime TotalTime DatePublished Description Images RecipeCategory Keywords RecipeIngredientQuantities RecipeIngredientParts AggregatedRating ReviewCount Calories FatContent SaturatedFatContent CholesterolContent SodiumContent CarbohydrateContent FiberContent SugarContent ProteinContent RecipeServings RecipeYield RecipeInstructions 38 Low-Fat Berry Blue Frozen Dessert 1533 Dancer PT24H PT45M PT24H45M 1999-08-09T21:46:00Z Make and share this Low-Fat Berry Blue Frozen Dessert recipe from Food.com. c("https://img.sndimg.com/food/image/upload/w_555,h_416,c_fit,fl_progressive,q_95/v1/img/recipes/38/YUeirxMLQaeE1h3v3qnM_229%20berry%20blue%20frzn%20dess.jpg", "https://img.sndimg.com/food/image/upload/w_555,h_416,c_fit,fl_progressive,q_95/v1/img/recipes/38/AFPDDHATWzQ0b1CDpDAT_255%20berry%20blue%20frzn%20dess.jpg", "https://img.sndimg.com/food/image/upload/w_555,h_416,c_fit,fl_progressive,q_95/v1/img/recipes/38/UYgf9nwMT2SGGJCuzILO_228%20berry%20blue%20frzn%20dess.jpg", "https://img.sndimg.com/food/image/upload/w_555,h_416,c_fit,fl_progressive,q_95/v1/img/recipes/38/PeBMJN2TGSaYks2759BA_20140722_202142.jpg", 
"https://img.sndimg.com/food/image/upload/w_555,h_416,c_fit,fl_progressive,q_95/v1/img/recipes/38/picuaETeN.jpg", "https://img.sndimg.com/food/image/upload/w_555,h_416,c_fit,fl_progressive,q_95/v1/img/recipes/38/pictzvxW5.jpg") Frozen Desserts c("Dessert", "Low Protein", "Low Cholesterol", "Healthy", "Free Of...", "Summer", "Weeknight", "Freezer", "Easy") c("4", "1/4", "1", "1") c("blueberries", "granulated sugar", "vanilla yogurt", "lemon juice") 4.5 4 170.9 2.5 1.3 8 29.8 37.1 3.6 30.2 3.2 4 NA c("Toss 2 cups berries with sugar.", "Let stand for 45 minutes, stirring occasionally.", "Transfer berry-sugar mixture to food processor.", "Add yogurt and process until smooth.", "Strain through fine sieve. Pour into baking pan (or transfer to ice cream maker and process according to manufacturers' directions). Freeze uncovered until edges are solid but centre is soft. Transfer to processor and blend until smooth again.", "Return to pan and freeze until edges are solid.", "Transfer to processor and blend until smooth again.", 
"Fold in remaining 2 cups of blueberries.", "Pour into plastic mold and freeze overnight. Let soften slightly to serve.") 39 Biryani 1567 elly9812 PT25M PT4H PT4H25M 1999-08-29T13:12:00Z Make and share this Biryani recipe from Food.com. c("https://img.sndimg.com/food/image/upload/w_555,h_416,c_fit,fl_progressive,q_95/v1/img/recipes/39/picM9Mhnw.jpg", "https://img.sndimg.com/food/image/upload/w_555,h_416,c_fit,fl_progressive,q_95/v1/img/recipes/39/picHv4Ocr.jpg") Chicken Breast c("Chicken Thigh & Leg", "Chicken", "Poultry", "Meat", "Asian", "Indian", "Weeknight", "Stove Top") c("1", "4", "2", "2", "8", "1/4", "8", "1/2", "1", "1", "1/4", "1/4", "1/2", "1/4", "2", "3", NA, "2", "1", "1", "8", "2", "1/3", "1/3", "1/3", "6") c("saffron", "milk", "hot green chili peppers", "onions", "garlic", "clove", "peppercorns", "cardamom seed", "cumin seed", "poppy seed", "mace", "cilantro", "mint leaf", "fresh lemon juice", "plain yogurt", "boneless chicken", "salt", "ghee", "onion", "tomatoes", "basmati rice", "long-grain rice", "raisins", "cashews", "eggs") 3 1 1110.7 58.8 16.6 372.8 368.4 84.4 9 20.4 63.4 6 NA c("Soak saffron in warm milk for 5 minutes and puree in blender.", "Add chiles, onions, ginger, garlic, cloves, peppercorns, cardamom seeds, cinnamon, coriander and cumin seeds, poppy seeds, nutmeg, mace, cilantro or mint leaves and lemon juice. Blend into smooth paste. Put paste into large bowl, add yogurt and mix well.", "Marinate chicken in yogurt mixture with salt, covered for at least 2 - 6 hours in refrigerator.", "In skillet. heat oil over medium heat for 1 minute. Add ghee and 15 seconds later add onion and fry for about8 minutes.", 
"Reserve for garnish.", "In same skillet, cook chicken with its marinade with tomatoes for about 10 minutes over medium heat, uncovered.", 

In [0]:
recipes_clean = spark.sql("""
select RecipeId, Description, RecipeInstructions, ReviewCount, CookTime, PrepTime, RecipeCategory, RecipeIngredientParts, AggregatedRating, Calories, FatContent, SaturatedFatContent, CholesterolContent, SodiumContent, CarbohydrateContent, FiberContent, SugarContent, ProteinContent, RecipeServings 
from recipes
where AggregatedRating != 'NA' and ReviewCount > 1
""")

In [0]:
# recipes_clean = spark.sql("""
# select RecipeId, Description, RecipeInstructions, ReviewCount, CookTime, PrepTime, RecipeCategory, RecipeIngredientParts, AggregatedRating, Calories, FatContent, SaturatedFatContent, CholesterolContent, SodiumContent, CarbohydrateContent, FiberContent, SugarContent, ProteinContent, RecipeServings 
# from recipes
# where AggregatedRating != 'NA'
# """)

In [0]:
recipes_clean.createOrReplaceTempView("recipes_clean")

# Feature processing

In [0]:
### Feature: CookDuration, PrepDuration
recipes_clean = recipes_clean.withColumn('CookHours', F.regexp_extract(F.col('CookTime'), '(\d+)(?=H)', 0).cast('int'))
recipes_clean = recipes_clean.withColumn('CookMinutes', F.regexp_extract(F.col('CookTime'), '(\d+)(?=M)', 0).cast('int'))
recipes_clean = recipes_clean.fillna({'CookHours': 0, 'CookMinutes': 0})
recipes_clean = recipes_clean.withColumn('CookDuration', recipes_clean['CookHours'] * 60 + recipes_clean['CookMinutes'])

recipes_clean = recipes_clean.withColumn('PrepHours', F.regexp_extract(F.col('PrepTime'), '(\d+)(?=H)', 0).cast('int'))
recipes_clean = recipes_clean.withColumn('PrepMinutes', F.regexp_extract(F.col('PrepTime'), '(\d+)(?=M)', 0).cast('int'))
recipes_clean = recipes_clean.fillna({'PrepHours': 0, 'PrepMinutes': 0})
recipes_clean = recipes_clean.withColumn('PrepDuration', recipes_clean['PrepHours'] * 60 + recipes_clean['PrepMinutes'])

recipes_clean = recipes_clean.drop(*['CookTime', 'CookHours', 'CookMinutes', 'PrepTime', 'PrepHours', 'PrepMinutes'])

### Feature: DescriptionLen
recipes_clean = recipes_clean.withColumn('DescriptionLen', F.length(recipes_clean['Description']))
recipes_clean = recipes_clean.drop('Description')

### Feature: RecipeIngredientPartsCount
recipes_clean = recipes_clean.withColumn('RecipeIngredientPartsCount', F.size(F.split(F.col('RecipeIngredientParts'), ',')))
recipes_clean = recipes_clean.drop('RecipeIngredientParts')

### Feature: RecipeInstructionSteps
recipes_clean = recipes_clean.withColumn('RecipeInstructionSteps', F.size(F.split(F.col('RecipeInstructions'), ',')))
recipes_clean = recipes_clean.drop('RecipeInstructions')

In [0]:
### Aggregate RecipeCategory
category_counts = recipes_clean.groupBy('RecipeCategory').agg(F.countDistinct('RecipeId').alias('CategoryCount'))
recipes_clean = recipes_clean.join(category_counts, on = 'RecipeCategory', how = 'left')
recipes_clean = recipes_clean.withColumn('RecipeCategory', F.when(F.col('CategoryCount') < 500, 'Other').otherwise(F.col('RecipeCategory')))
recipes_clean = recipes_clean.drop('CategoryCount')
recipes_clean.groupBy('RecipeCategory').agg(F.countDistinct('RecipeId').alias('count')).orderBy(F.desc('count')).show(50,truncate=False)

### Feature: dummy variables based on RecipeCategory
indexer = StringIndexer(inputCol='RecipeCategory', outputCol='RecipeCategoryIndex')
recipes_clean = indexer.fit(recipes_clean).transform(recipes_clean)
encoder = OneHotEncoder(inputCol='RecipeCategoryIndex', outputCol='RecipeCategoryVec')
recipes_clean = encoder.fit(recipes_clean).transform(recipes_clean)

recipe_category_index_mapping = recipes_clean.select(['RecipeCategory', 'RecipeCategoryIndex']).distinct()
# display(recipe_category_index_mapping)

+----------------+-----+
|RecipeCategory  |count|
+----------------+-----+
|Other           |17860|
|Dessert         |17278|
|Lunch/Snacks    |11701|
|One Dish Meal   |11147|
|Vegetable       |9546 |
|Breakfast       |7122 |
|Beverages       |5567 |
|Chicken         |5076 |
|Pork            |4559 |
|Breads          |4380 |
|Potato          |4297 |
|Chicken Breast  |4275 |
|Quick Breads    |4217 |
|Meat            |4096 |
|Sauces          |3875 |
|Cheese          |3102 |
|Bar Cookie      |2561 |
|Drop Cookies    |2404 |
|Pie             |2375 |
|Yeast Breads    |2263 |
|< 60 Mins       |2050 |
|Stew            |1964 |
|< 30 Mins       |1940 |
|Salad Dressings |1684 |
|Candy           |1684 |
|Beans           |1669 |
|Low Protein     |1622 |
|< 15 Mins       |1557 |
|Spreads         |1491 |
|Smoothies       |1321 |
|Poultry         |1158 |
|Steak           |1151 |
|Frozen Desserts |1101 |
|Onions          |1096 |
|Savory Pies     |1040 |
|Curries         |1001 |
|Rice            |998  |


In [0]:
### prepare response variable
### try multi class classification
# recipes_clean = recipes_clean.withColumn('AggregatedRatingBucket', F.when(recipes_clean['AggregatedRating'].isin([1, 1.5, 2, 2.5]), 'low').when(recipes_clean['AggregatedRating'].isin([3, 3.5, 4]), 'medium').otherwise('high'))
# recipes_clean = recipes_clean.withColumn('AggregatedRatingBucket', F.when(recipes_clean['AggregatedRatingBucket']=='low', '1').when(recipes_clean['AggregatedRatingBucket'] == 'medium', '2').otherwise('3'))
### change to binary class classification
recipes_clean.groupBy('AggregatedRating').count().orderBy('AggregatedRating').show()
recipes_clean = recipes_clean.withColumn('AggregatedRatingBucket', F.when(recipes_clean['AggregatedRating'].isin([1, 1.5, 2, 2.5, 3, 3.5]), 'low').otherwise('high'))
recipes_clean = recipes_clean.withColumn('AggregatedRatingBucket', F.when(recipes_clean['AggregatedRatingBucket']=='low', '1').otherwise('0'))
recipes_clean = recipes_clean.withColumn('AggregatedRatingBucket', recipes_clean['AggregatedRatingBucket'].cast(IntegerType()))
recipes_clean = recipes_clean.drop('AggregatedRating')

+----------------+------+
|AggregatedRating| count|
+----------------+------+
|               1|   225|
|             1.5|    76|
|               2|   328|
|             2.5|   673|
|               3|  2755|
|             3.5|  3978|
|               4| 16063|
|             4.5| 34330|
|               5|109201|
+----------------+------+



In [0]:
recipes_clean.groupBy('AggregatedRatingBucket').count().orderBy('AggregatedRatingBucket').show()

+----------------------+------+
|AggregatedRatingBucket| count|
+----------------------+------+
|                     0|159594|
|                     1|  8035|
+----------------------+------+



In [0]:
### convert string columns to numerical columns
cols_to_convert = ['DescriptionLen', 'RecipeInstructionSteps', 'Calories', 'FatContent', 'SaturatedFatContent', 'CholesterolContent', 'SodiumContent', 'CarbohydrateContent', 'FiberContent', 'SugarContent', 'ProteinContent', 'RecipeServings']
for col_name in cols_to_convert:
    recipes_clean = recipes_clean.withColumn(col_name, recipes_clean[col_name].cast("float"))

In [0]:
recipes_clean.select(cols_to_convert).describe().show()

+-------+------------------+----------------------+------------------+----------------+-------------------+------------------+------------------+-------------------+-----------------+-----------------+------------------+------------------+
|summary|    DescriptionLen|RecipeInstructionSteps|          Calories|      FatContent|SaturatedFatContent|CholesterolContent|     SodiumContent|CarbohydrateContent|     FiberContent|     SugarContent|    ProteinContent|    RecipeServings|
+-------+------------------+----------------------+------------------+----------------+-------------------+------------------+------------------+-------------------+-----------------+-----------------+------------------+------------------+
|  count|            167629|                167629|            167629|          167629|             167629|            167629|            167629|             167629|           167629|           167629|            167629|            106357|
|   mean|202.45951476176558|    12.37081

### check missing rate

In [0]:
# missing_rates = recipes_clean.select([(F.count(F.when(F.col(c).isNull(), c))/recipes_clean.count()).alias(c) for c in cols_to_convert]).show()

In [0]:
recipes_clean = recipes_clean.fillna(0, subset=cols_to_convert)

In [0]:
recipes_clean = recipes_clean.drop(*['RecipeCategory', 'ReviewCount', 'RecipeId'])

### check association direction between features and response

In [0]:
# feature_cols = ['DescriptionLen', 'RecipeInstructionSteps', 'Calories', 'FatContent', 'SaturatedFatContent', 'CholesterolContent', 'SodiumContent', 
#     'CarbohydrateContent', 'FiberContent', 'SugarContent', 'ProteinContent', 'RecipeServings', 
#     'CookDuration', 'PrepDuration', 'RecipeIngredientPartsCount'] 
# response_col = 'AggregatedRatingBucket'

# for feature_col in feature_cols:
#     correlation = recipes_clean.stat.corr(feature_col, response_col)
#     print(f"Correlation between {feature_col} and {response_col}: {round(correlation, 4)}")

# Model building

### upsampling minority class

In [0]:
# # Calculating the ratio of weights to oversample
# score1_df = recipes_clean.filter(F.col("AggregatedRatingBucket") == 1)
# score2_df = recipes_clean.filter(F.col("AggregatedRatingBucket") == 2)
# score3_df = recipes_clean.filter(F.col("AggregatedRatingBucket") == 3)

# ratio_3_1 = int(score3_df.count()/score1_df.count())
# ratio_3_2 = int(score3_df.count()/score2_df.count())

# print("ratio_3_1: {}".format(ratio_3_1))
# print("ratio_3_2: {}".format(ratio_3_2))

# # duplicate the minority rows in Successful state
# up1_df = score1_df.withColumn("dummy", F.explode(F.array([F.lit(x) for x in range(int(ratio_3_1+1))]))).drop('dummy')
# # combine both oversampled successful rows and previous majority rows 
# score3_df = score3_df.unionAll(up1_df)

# # duplicate the minority rows in Successful state
# up2_df = score2_df.withColumn("dummy", F.explode(F.array([F.lit(x) for x in range(int(ratio_3_2+1))]))).drop('dummy')
# # combine both oversampled successful rows and previous majority rows 
# score3_df = score3_df.unionAll(up2_df)

# recipes_clean_up = score3_df
# # recipes_clean_up.groupBy('AggregatedRatingBucket').count().orderBy('AggregatedRatingBucket').show()

In [0]:
# # Calculating the ratio of weights to oversample
# score0_df = recipes_clean.filter(F.col("AggregatedRatingBucket") == 0)
# score1_df = recipes_clean.filter(F.col("AggregatedRatingBucket") == 1)

# ratio_1_0 = int(score1_df.count()/score0_df.count())

# print("ratio_1_0: {}".format(ratio_1_0))

# # duplicate the minority rows in Successful state
# up0_df = score0_df.withColumn("dummy", F.explode(F.array([F.lit(x) for x in range(int(ratio_1_0+1))]))).drop('dummy')
# # combine both oversampled successful rows and previous majority rows 
# score1_df = score1_df.unionAll(up0_df)

# recipes_clean_up = score1_df
# # recipes_clean_up.groupBy('AggregatedRatingBucket').count().orderBy('AggregatedRatingBucket').show()

### split train and test data

In [0]:
### use upsampling
# train, test = recipes_clean_up.randomSplit([0.7, 0.3], seed = 123)

### not use upsampling
train, test = recipes_clean.randomSplit([0.7, 0.3], seed = 123)

### downsample majority class

In [0]:
# train.groupBy('AggregatedRatingBucket').count().show()

In [0]:
score0_df = train.filter(F.col('AggregatedRatingBucket') == 0)
score1_df = train.filter(F.col('AggregatedRatingBucket') == 1)
ratio = int(score0_df.count()/score1_df.count())
print(ratio)

sampled_score0_df = score0_df.sample(False, 1/ratio)
train_down = sampled_score0_df.unionAll(score1_df)

19


## random forest

In [0]:
assembler = VectorAssembler(
    inputCols=['DescriptionLen', 'RecipeInstructionSteps', 'Calories', 'FatContent', 'SaturatedFatContent', 'CholesterolContent', 'SodiumContent', 
    'CarbohydrateContent', 'FiberContent', 'SugarContent', 'ProteinContent', 'RecipeServings', 
    'CookDuration', 'PrepDuration', 'RecipeIngredientPartsCount', 'RecipeCategoryVec'],
    outputCol='features')

rf = RandomForestClassifier(labelCol="AggregatedRatingBucket", featuresCol="features", numTrees=500)
pipeline = Pipeline(stages=[assembler, rf])
model = pipeline.fit(train)
predictions = model.transform(test)

In [0]:
# AUC
evaluator = MulticlassClassificationEvaluator(predictionCol="prediction", labelCol='AggregatedRatingBucket')
print('Test Area Under ROC', evaluator.evaluate(predictions))

Test Area Under ROC 0.9294897348025476


In [0]:
display(predictions)

Calories FatContent SaturatedFatContent CholesterolContent SodiumContent CarbohydrateContent FiberContent SugarContent ProteinContent RecipeServings CookDuration PrepDuration DescriptionLen RecipeIngredientPartsCount RecipeInstructionSteps RecipeCategoryIndex RecipeCategoryVec AggregatedRatingBucket features rawPrediction probability prediction 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0 5 103.0 3 5.0 28.0 Map(vectorType -> sparse, length -> 58, indices -> List(28), values -> List(1.0)) 0 Map(vectorType -> sparse, length -> 73, indices -> List(0, 1, 13, 14, 43), values -> List(103.0, 5.0, 5.0, 3.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(475.9840479444306, 24.01595205556923)) Map(vectorType -> dense, length -> 2, values -> List(0.9519680958888614, 0.048031904111138474)) 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0 10 380.0 1 4.0 4.0 Map(vectorType -> sparse, length -> 58, indices -> List(4), values -> List(1.0)) 0 Map(vectorType -> sparse, length -> 73, indices -> List(0, 1, 13, 14, 19), values -> List(380.0, 4.0, 10.0, 1.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(476.6254546792619, 23.37454532073781)) Map(vectorType -> dense, length -> 2, values -> List(0.9532509093585243, 0.046749090641475644)) 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0 960 358.0 1 9.0 32.0 Map(vectorType -> sparse, length -> 58, indices -> List(32), values -> List(1.0)) 0 Map(vectorType -> sparse, length -> 73, indices -> List(0, 1, 13, 14, 47), values -> List(358.0, 9.0, 960.0, 1.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(476.3657220901832, 23.63427790981634)) Map(vectorType -> dense, length -> 2, values -> List(0.9527314441803674, 0.04726855581963273)) 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 5 5 116.0 5 10.0 4.0 Map(vectorType -> sparse, length -> 58, indices -> List(4), values -> List(1.0)) 0 Map(vectorType -> sparse, length -> 73, indices -> List(0, 1, 12, 13, 14, 19), values -> List(116.0, 10.0, 5.0, 5.0, 5.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(475.7549617264586, 24.2450382735416)) Map(vectorType -> dense, length -> 2, values -> List(0.9515099234529169, 0.048490076547083184)) 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 10 10 62.0 3 3.0 4.0 Map(vectorType -> sparse, length -> 58, indices -> List(4), values -> List(1.0)) 0 Map(vectorType -> sparse, length -> 73, indices -> List(0, 1, 12, 13, 14, 19), values -> List(62.0, 3.0, 10.0, 10.0, 3.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(475.3984235654502, 24.601576434549937)) Map(vectorType -> dense, length -> 2, values -> List(0.9507968471309002, 0.04920315286909986)) 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 15 10 483.0 4 7.0 4.0 Map(vectorType -> sparse, length -> 58, indices -> List(4), values -> List(1.0)) 0 Map(vectorType -> sparse, length -> 73, indices -> List(0, 1, 12, 13, 14, 19), values -> List(483.0, 7.0, 15.0, 10.0, 4.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(475.5092599377557, 24.490740062243955)) Map(vectorType -> dense, length -> 2, values -> List(0.951018519875512, 0.04898148012448794)) 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 30 15 217.0 1 5.0 32.0 Map(vectorType -> sparse, length -> 58, indices -> List(32), values -> List(1.0)) 0 Map(vectorType -> sparse, length -> 73, indices -> List(0, 1, 12, 13, 14, 47), values -> List(217.0, 5.0, 30.0, 15.0, 1.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(475.1640472661522, 24.83595273384751)) Map(vectorType -> dense, length -> 2, values -> List(0.9503280945323049, 0.049671905467695045)) 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 0 3 336.0 1 2.0 32.0 Map(vectorType -> sparse, length -> 58, indices -> List(32), values -> List(1.0)) 0 Map(vectorType -> sparse, length -> 73, indices -> List(0, 1, 11, 13, 14, 47), values -> List(336.0, 2.0, 1.0, 3.0, 1.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(476.53621610442343, 23.463783895576114)) Map(vectorType -> dense, length -> 2, values -> List(0.9530

In [0]:
# Accuracy
evaluator = MulticlassClassificationEvaluator(
    labelCol="AggregatedRatingBucket", predictionCol="prediction", metricName="accuracy")
accuracy = evaluator.evaluate(predictions)

print("Test Accuracy = %g" % accuracy)

In [0]:
# Confustion matrix
preds_and_labels = predictions.select(['prediction','AggregatedRatingBucket']).withColumn('AggregatedRatingBucket', F.col('AggregatedRatingBucket').cast(FloatType())).orderBy('prediction')

preds_and_labels = preds_and_labels.select(['prediction','AggregatedRatingBucket'])

metrics = MulticlassMetrics(preds_and_labels.rdd.map(tuple))

print(metrics.confusionMatrix().toArray())

In [0]:
# Precision and recall
# Class-0
print('\n--------------Class-0----------------')
print('Precision          :', round(metrics.precision(0), 3))
print('recall             :', round(metrics.recall(0), 3))

# Class-1
print('\n--------------Class-1----------------')
print('Precision          :', round(metrics.precision(1), 3))
print('recall             :', round(metrics.recall(1), 3))

# # Class-3
# print('\n--------------Class-3----------------')
# print('Precision          :', round(metrics.precision(3), 3))
# print('recall             :', round(metrics.recall(3), 3))

# Overall Accuracy
print('\n Overall Accuracy:', round(metrics.accuracy, 3))

In [0]:
### Plot feature importance for top 20 variables
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

# Get feature importances from the model
feature_importances = model.stages[-1].featureImportances
print(len(feature_importances))

# Convert indices to feature names
feature_names = ['DescriptionLen', 'RecipeInstructionSteps', 'Calories', 'FatContent', 'SaturatedFatContent', 'CholesterolContent', 'SodiumContent', 
    'CarbohydrateContent', 'FiberContent', 'SugarContent', 'ProteinContent', 'RecipeServings', 
    'CookDuration', 'PrepDuration', 'RecipeIngredientPartsCount', 'RecipeCategoryVec']  # replace with your feature names

num_binary_features = len(feature_importances) - 15
binary_feature_names = ['RecipeCategoryVec_' + str(i) for i in range(num_binary_features)]
feature_names = feature_names + binary_feature_names

importances = {feature_names[i]: importance for i, importance in enumerate(feature_importances)}

# Convert to pandas DataFrame for easier plotting
importances_df = pd.DataFrame(list(importances.items()), columns=['Feature', 'Importance'])
importances_df = importances_df.sort_values(by='Importance', ascending=False)
importances_df = importances_df.iloc[0:20, :]
# Plot feature importances
plt.figure(figsize=(10, 6))
plt.barh(importances_df['Feature'], importances_df['Importance'], color='skyblue')
plt.xlabel("Importance")
plt.title("Feature Importance")
plt.gca().invert_yaxis()
plt.show()

### multinomial logistic regression

In [0]:
assembler = VectorAssembler(
    inputCols=['DescriptionLen', 'RecipeInstructionSteps', 'Calories', 'FatContent', 'SaturatedFatContent', 'CholesterolContent', 'SodiumContent', 
    'CarbohydrateContent', 'FiberContent', 'SugarContent', 'ProteinContent', 'RecipeServings', 
    'CookDuration', 'PrepDuration', 'RecipeIngredientPartsCount', 'RecipeCategoryVec'],
    outputCol='features')

lr = LogisticRegression(featuresCol = 'features', labelCol = 'AggregatedRatingBucket', maxIter=10)

pipeline = Pipeline(stages=[assembler, lr])
model = pipeline.fit(train)
lrModel = model.stages[-1]

predictions = model.transform(test)

In [0]:
# Print the coefficients and intercept for multinomial logistic regression
print("Coefficients: \n" + str(lrModel.coefficientMatrix))
print("Intercept: " + str(lrModel.interceptVector))

In [0]:
# Getting the training summary
trainingSummary = lrModel.summary

In [0]:
# AUC
evaluator = MulticlassClassificationEvaluator(predictionCol="prediction", labelCol='AggregatedRatingBucket')
print('Test Area Under ROC', evaluator.evaluate(predictions))

In [0]:
# Accuracy
evaluator = MulticlassClassificationEvaluator(
    labelCol="AggregatedRatingBucket", predictionCol="prediction", metricName="accuracy")
accuracy = evaluator.evaluate(predictions)

print("Test Accuracy = %g" % accuracy)

In [0]:
# Confusion matrix
preds_and_labels = predictions.select(['prediction','AggregatedRatingBucket']).withColumn('AggregatedRatingBucket', F.col('AggregatedRatingBucket').cast(FloatType())).orderBy('prediction')

#select only prediction and label columns
preds_and_labels = preds_and_labels.select(['prediction','AggregatedRatingBucket'])

metrics = MulticlassMetrics(preds_and_labels.rdd.map(tuple))

print(metrics.confusionMatrix().toArray())

In [0]:
# Precision and recall
# Class-0
print('\n--------------Class-0----------------')
print('Precision          :', round(metrics.precision(0), 3))
print('recall             :', round(metrics.recall(0), 3))

# Class-1
print('\n--------------Class-1----------------')
print('Precision          :', round(metrics.precision(1), 3))
print('recall             :', round(metrics.recall(1), 3))

# Overall Accuracy
print('\n Overall Accuracy:', round(metrics.accuracy, 3))

In [0]:
# # for multiclass, we can inspect metrics on a per-label basis
# print("False positive rate by label:")
# for i, rate in enumerate(trainingSummary.falsePositiveRateByLabel):
#     print("label %d: %s" % (i, round(rate, 4)))

# print("True positive rate by label:")
# for i, rate in enumerate(trainingSummary.truePositiveRateByLabel):
#     print("label %d: %s" % (i, round(rate, 4)))

# print("Precision by label:")
# for i, prec in enumerate(trainingSummary.precisionByLabel):
#     print("label %d: %s" % (i, round(prec, 4)))

# print("Recall by label:")
# for i, rec in enumerate(trainingSummary.recallByLabel):
#     print("label %d: %s" % (i, round(rec, 4)))

# print("F-measure by label:")
# for i, f in enumerate(trainingSummary.fMeasureByLabel()):
#     print("label %d: %s" % (i, round(f, 4)))

# accuracy = trainingSummary.accuracy
# falsePositiveRate = trainingSummary.weightedFalsePositiveRate
# truePositiveRate = trainingSummary.weightedTruePositiveRate
# fMeasure = trainingSummary.weightedFMeasure()
# precision = trainingSummary.weightedPrecision
# recall = trainingSummary.weightedRecall
# print("Accuracy: %s\nFPR: %s\nTPR: %s\nF-measure: %s\nPrecision: %s\nRecall: %s"
#           % (round(accuracy, 4), round(falsePositiveRate, 4), round(truePositiveRate, 4), round(fMeasure, 4), round(precision, 4), round(recall, 4)))